In [53]:

from llama_index.readers.obsidian import ObsidianReader
import openai
from llama_index.core.memory.chat_memory_buffer import MessageRole
from llama_index.core import SimpleDirectoryReader, KnowledgeGraphIndex, VectorStoreIndex
from llama_index.core.graph_stores import SimpleGraphStore
from llama_index.core.storage.docstore import SimpleDocumentStore
from llama_index.core import Document, PropertyGraphIndex
from llama_index.core.storage.index_store import SimpleIndexStore
from llama_index.core.vector_stores import SimpleVectorStore
from llama_index.core import Settings
from IPython.display import Markdown, display
from llama_index.llms.ollama import Ollama
from tqdm.notebook import tqdm
import time
import os
from llama_index.core.llms import ChatMessage
from llama_index.core import StorageContext
from llama_index.llms.ollama import Ollama
from llama_index.embeddings.ollama import OllamaEmbedding
from llama_index.embeddings.huggingface import HuggingFaceEmbedding
from llama_index.embeddings.openai import OpenAIEmbedding
from llama_index.llms.openai import OpenAI
from llama_index.core.memory import ChatMemoryBuffer
import logging
import sys
import ipywidgets as widgets
import json
from llama_index.core.callbacks import CallbackManager
from llama_index.core.callbacks import LlamaDebugHandler
from llama_index.core import ServiceContext
from llama_index.core.query_engine import RetrieverQueryEngine
from llama_index.core.retrievers import KnowledgeGraphRAGRetriever
from llama_index.core.indices.property_graph import (
    SimpleLLMPathExtractor,
    SchemaLLMPathExtractor,
    DynamicLLMPathExtractor,
)
import yaml
from dotenv import load_dotenv

In [54]:
from llama_index.core import (
    load_index_from_storage,
    load_indices_from_storage,
    load_graph_from_storage,
)

In [55]:
import nest_asyncio

nest_asyncio.apply()

In [56]:
logging.basicConfig(stream=sys.stdout, level=logging.INFO)
logging.getLogger().addHandler(logging.StreamHandler(stream=sys.stdout))

# Build a simple directory

In [57]:
simple_glossary = SimpleDirectoryReader(
    r"/Users/arthursarazin/Documents/coreandgraphs/graphandvisualize/graph"
).load_data()

# Upload Obsidian vault files

#### Using Obsidian reader from LLama Index

In [58]:
#locate obsidian files that make your graph
filepath = r"/Users/arthursarazin/Documents/coreandgraphs/graphandvisualize/graph"

#load the graph files 
graph_files = ObsidianReader(filepath).load_data()
print(list(graph_files))

[Document(id_='0a9a0ec7-4940-44c0-b127-dbaa69f0aefe', embedding=None, metadata={}, excluded_embed_metadata_keys=[], excluded_llm_metadata_keys=[], relationships={}, metadata_template='{key}: {value}', metadata_separator='\n', text_resource=MediaResource(embeddings=None, data=None, text="Quels critères pour dire que des données sont de qualité ?\n- Exactitude : les données sont justes et cohérentes\n- Complétude : le jeu de données est complet \n- Pertinence : les données que l'on a sont elles pertinentes pour répondre à nos besoins (et par extension ceux du client ?)\n\nDes données de bonnes qualités sont essentielles pour avoir des donnes fiables ", mimetype=None, path=None, url=None), image_resource=None, audio_resource=None, video_resource=None, text_template='{metadata_str}\n\n{content}'), Document(id_='db7bad69-0c19-4aba-abc6-9dcf4a986ba1', embedding=None, metadata={}, excluded_embed_metadata_keys=[], excluded_llm_metadata_keys=[], relationships={}, metadata_template='{key}: {valu

# Using manual code to create specific ontology

In [59]:
# Fonction pour extraire les métadonnées YAML et le titre d'un fichier Markdown
def extract_metadata_and_title(file_path):
    with open(file_path, 'r', encoding='utf-8') as f:
        content = f.read()
        # Recherchez la section YAML (entre `---` au début et à la fin)
        if content.startswith("---"):
            try:
                yaml_block = content.split("---", 2)[1]
                metadata = yaml.safe_load(yaml_block)
                return os.path.basename(file_path).replace(".md", ""), metadata
            except Exception as e:
                print(f"Erreur lors de l'extraction des métadonnées de {file_path}: {e}")
                return None, None
        return os.path.basename(file_path).replace(".md", ""), None

# Parcourir les fichiers Obsidian et créer des entités et relations
def process_obsidian_notes(directory):
    entities = []
    relations = []
    
    for root, _, files in os.walk(directory):
        for file in files:
            if file.endswith(".md"):
                file_path = os.path.join(root, file)
                title, metadata = extract_metadata_and_title(file_path)
                if title:
                    # Ajouter l'entité basée sur le titre
                    entities.append({"name": title})
                    
                    # Ajouter les relations basées sur les propriétés YAML
                    if metadata:
                        for key, value in metadata.items():
                            relations.append({
                                "type": key,  # Nom de la propriété comme relation
                                "source": title,  # Titre du fichier comme entité source
                                "target": value,  # Valeur de la propriété comme entité cible
                            })
    return entities, relations



In [60]:
# Exemple d'utilisation
obsidian_dir = r"C:\Users\asarazin\OneDrive - Veltys Max\Documents\documente-marcel\graph"
entities, relations = process_obsidian_notes(obsidian_dir)

print(relations)

[]


# Set LLM (OpenAI)

In [61]:
load_dotenv()  # Charge les variables depuis le fichier .env
api_key = os.getenv("OPENAI_API_KEY_UP")
# Modifier ou ajouter une variable d'environnement
os.environ["OPENAI_API_KEY"] = api_key

In [62]:
llm = OpenAI(temperature=0, model="gpt-4o", max_tokens=3000)
Settings.llm = llm
Settings.chunk_size = 512

# Set local LLM for embeddings ()

In [63]:
# bge-base embedding model
Settings.embed_model = HuggingFaceEmbedding(model_name="BAAI/bge-base-en-v1.5")
#Settings.embed_model = OpenAIEmbedding(model="text-embedding-3-small")


INFO:sentence_transformers.SentenceTransformer:Load pretrained SentenceTransformer: BAAI/bge-base-en-v1.5
Load pretrained SentenceTransformer: BAAI/bge-base-en-v1.5
Load pretrained SentenceTransformer: BAAI/bge-base-en-v1.5
Load pretrained SentenceTransformer: BAAI/bge-base-en-v1.5
INFO:sentence_transformers.SentenceTransformer:2 prompts are loaded, with the keys: ['query', 'text']
2 prompts are loaded, with the keys: ['query', 'text']
2 prompts are loaded, with the keys: ['query', 'text']
2 prompts are loaded, with the keys: ['query', 'text']


# Set LLM for chat  (Local)

In [64]:
#llm = Ollama(model="tinyllama", request_timeout=120.0)
#Settings.llm = llm
#Settings.chunk_size = 512

# Test LLM

In [65]:
messages = [
    ChatMessage(
        role="system", content="You are a data governance consultant"
    ),
    ChatMessage(role="user", content="What's your favorite data tool ?"),
]
resp = llm.chat(messages)
print(resp)

INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
assistant: As a data governance consultant, I don't have personal preferences or favorites. However, I can tell you about some popular data tools that are widely used in the industry for various purposes:

1. **Collibra**: Known for its data governance and cataloging capabilities, Collibra helps organizations manage their data assets, ensuring compliance and improving data quality.

2. **Informatica**: Offers a suite of data management tools, including data integration, data quality, and master data management, which are essential for effective data governance.

3. **Alation**: A leader in data cataloging, Alation helps organizations discover, understand, and m

In [66]:
# Instantiate vector store
simple_glossary = SimpleDirectoryReader(
    r"/Users/arthursarazin/Documents/coreandgraphs/graphandvisualize/graph"
)

# Instantiate graph store 

In [67]:
graph_store = SimpleGraphStore()
graph_storage_context = StorageContext.from_defaults(graph_store=graph_store)

# Instantiate ontology store

In [68]:
onto_store = SimpleGraphStore()
onto_storage_context = StorageContext.from_defaults(graph_store=onto_store)

# Construct Index

## Construct Vector Store Index

In [69]:
vector_index = VectorStoreIndex.from_documents(
    documents = simple_glossary.load_data(),
    show_progress=True)

Parsing nodes:   0%|          | 0/44 [00:00<?, ?it/s]

Generating embeddings:   0%|          | 0/44 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [70]:
# save index to disk
vector_index.set_index_id("vector_index")
vector_index.storage_context.persist("vector")

## Construct knowledge graph index 

In [71]:
def process_document(doc):
    # This function will be called for each document
    print(f"Processing document: {doc.doc_id}")
    return doc

In [72]:
# Assuming you have your graph files loaded
print(f"Starting to process {len(graph_files)} documents...")

Starting to process 44 documents...


In [73]:
# Wrap your document processing in a progress bar
graph_index = KnowledgeGraphIndex.from_documents(
        documents=[process_document(doc) for doc in graph_files],  # process one document at a time
        max_triplets_per_chunk=2,
        storage_context=graph_storage_context,
        include_embeddings=True,
    show_progress=True,
)


Processing document: 0a9a0ec7-4940-44c0-b127-dbaa69f0aefe
Processing document: db7bad69-0c19-4aba-abc6-9dcf4a986ba1
Processing document: 5dad3bd5-8969-44a4-aeb6-41265dbb5bde
Processing document: 4d4ed8c1-1653-4ae5-962d-539e5449a9a2
Processing document: aa08ef9f-10f2-4a4c-9446-a8dd22a4c299
Processing document: 3afb43b4-e8ea-47bf-b736-619406e8705a
Processing document: 48642eac-e872-447a-8581-d43b2975adcd
Processing document: eaf9c55f-5d79-472a-bef7-0e13e4d47e42
Processing document: be9b35c6-2a88-4bbf-9582-c9ef60f8e119
Processing document: 0e6ea860-260c-41e6-9d50-24fd581f8f08
Processing document: 88363a01-48b8-4cc1-ba8f-88d5feb89da7
Processing document: f23f2170-b970-4fde-b10f-73982a35a536
Processing document: ff95436e-09eb-41cf-9605-4b8babd257e9
Processing document: a237a273-0bb2-46c0-a294-bdd2d6b51331
Processing document: 0c082b03-8024-4177-a89d-efaa66570d73
Processing document: e457dbdc-2988-4a93-9712-f507a5a6d014
Processing document: d12e1333-6468-4460-b633-f87ec4e08f37
Processing doc

Parsing nodes:   0%|          | 0/44 [00:00<?, ?it/s]

Processing nodes:   0%|          | 0/44 [00:00<?, ?it/s]

INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


Generating embeddings:   0%|          | 0/2 [00:00<?, ?it/s]

...

Generating embeddings:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


Generating embeddings:   0%|          | 0/2 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

In [74]:
print(graph_index)

In [75]:
graph_index.set_index_id("graph_index")
graph_index.storage_context.persist("knowledge_graph")
graph_storage_context.persist(persist_dir="knowledge_graph")


## Construct knowledge with ontology as assistant

In [76]:
onto_store = SimpleGraphStore()
onto_storage_context = StorageContext.from_defaults(graph_store=onto_store)

In [77]:
# Configurer DynamicLLMPathExtractor avec les entités et relations extraites
kg_extractor = DynamicLLMPathExtractor(
    llm=llm,
    max_triplets_per_chunk=20,
    num_workers=4,
    allowed_entity_types=None,  # Si vous ne limitez pas les types d'entités
    allowed_relation_types=None,  # Si vous ne limitez pas les types de relations
    allowed_entity_props=None,
    allowed_relation_props=None,
)

In [78]:
# Résumé des entités et relations extraites
print("Entités :")
for entity in entities:
    print(entity)

print("\nRelations :")
for relation in relations:
    print(relation)

Entités :

Relations :


In [79]:
onto_index = PropertyGraphIndex.from_documents(
    documents=[process_document(doc) for doc in graph_files],
    llm=llm,
    storage_context=onto_storage_context,
    embed_kg_nodes=True,
    kg_extractors=[kg_extractor],
    show_progress=True,
    graph_store=onto_store 

)

Processing document: 0a9a0ec7-4940-44c0-b127-dbaa69f0aefe
Processing document: db7bad69-0c19-4aba-abc6-9dcf4a986ba1
Processing document: 5dad3bd5-8969-44a4-aeb6-41265dbb5bde
Processing document: 4d4ed8c1-1653-4ae5-962d-539e5449a9a2
Processing document: aa08ef9f-10f2-4a4c-9446-a8dd22a4c299
Processing document: 3afb43b4-e8ea-47bf-b736-619406e8705a
Processing document: 48642eac-e872-447a-8581-d43b2975adcd
Processing document: eaf9c55f-5d79-472a-bef7-0e13e4d47e42
Processing document: be9b35c6-2a88-4bbf-9582-c9ef60f8e119
Processing document: 0e6ea860-260c-41e6-9d50-24fd581f8f08
Processing document: 88363a01-48b8-4cc1-ba8f-88d5feb89da7
Processing document: f23f2170-b970-4fde-b10f-73982a35a536
Processing document: ff95436e-09eb-41cf-9605-4b8babd257e9
Processing document: a237a273-0bb2-46c0-a294-bdd2d6b51331
Processing document: 0c082b03-8024-4177-a89d-efaa66570d73
Processing document: e457dbdc-2988-4a93-9712-f507a5a6d014
Processing document: d12e1333-6468-4460-b633-f87ec4e08f37
Processing doc

Parsing nodes:   0%|          | 0/44 [00:00<?, ?it/s]

Extracting and inferring knowledge graph from text:   0%|          | 0/44 [00:00<?, ?it/s]

INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"


Extracting and inferring knowledge graph from text:   2%|▏         | 1/44 [00:00<00:37,  1.14it/s]

...

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Batches:   0%|          | 0/1 [00:00<?, ?it/s]

Generating embeddings: 100%|██████████| 45/45 [00:56<00:00,  1.26s/it]


In [80]:
print(onto_storage_context)

StorageContext(docstore=<llama_index.core.storage.docstore.simple_docstore.SimpleDocumentStore object at 0x38ecbeb90>, index_store=<llama_index.core.storage.index_store.simple_index_store.SimpleIndexStore object at 0x38ecfbf50>, vector_stores={'default': SimpleVectorStore(stores_text=False, is_embedding_query=True, data=SimpleVectorStoreData(embedding_dict={'Exactitude': [0.014583703130483627, 0.010762425139546394, 0.04669114202260971, -0.018375495448708534, 0.011859133839607239, 0.06262987107038498, 0.04932396486401558, 0.019457513466477394, -0.029114864766597748, -0.020073438063263893, -0.016135020181536674, 0.010933596640825272, -0.07563892751932144, 0.019831642508506775, -0.030081050470471382, 0.06752508133649826, 0.05756658688187599, -0.001502222497947514, -0.0003874346730299294, -0.01616748981177807, 0.015820054337382317, 0.0069536129012703896, -0.023571016266942024, -0.024793893098831177, -0.0026123940479010344, 0.012884334661066532, -0.005004926584661007, -0.020395640283823013,

In [81]:
# save index to disk
onto_index.set_index_id("onto_index")
onto_index.storage_context.persist("onto_graph")
onto_storage_context.persist(persist_dir="onto_graph")